In [1]:
print("OK")

OK


In [2]:
pwd

'/Users/modakverma/Desktop/AI_Study_ChatBot/research'

In [3]:
import os
os.chdir("../")

In [4]:
from langchain.document_loaders import PyPDFLoader, DirectoryLoader
from langchain.text_splitter import RecursiveCharacterTextSplitter

In [6]:
def load_pdf_files(data):
    loader = DirectoryLoader(
        data,
        glob="*.pdf",
        loader_cls=PyPDFLoader
        
    )
    documents = loader.load()
    return documents

In [7]:
extracted_data = load_pdf_files("data")

In [10]:
extracted_data

[Document(metadata={'producer': 'Acrobat Distiller 10.1.16 (Macintosh)', 'creator': 'Adobe InDesign CS6 (Windows)', 'creationdate': '2017-08-08T11:22:14+01:00', 'author': 'Rafael C. Gonzalez', 'moddate': '2017-10-19T19:56:22+05:30', 'title': 'Digital Image Processing, 4e', 'trapped': '/False', 'source': 'data/1 Rafael C. Gonzales, Digital Image Processing.pdf', 'total_pages': 1022, 'page': 0, 'page_label': 'Cover'}, page_content='GLOBAL \nEDITION\nThis is a special edition of an established \ntitle widely used by colleges and universities \nthroughout the world. Pearson published this \nexclusive edition for the benefit of students \noutside the United States and Canada. If \nyou purchased this book within the United \nStates or Canada, you should be aware that \nit has been imported without the approval of \nthe Publisher or Author. The Global Edition \nis not supported in the United States and \nCanada.\nPearson Global Edition\nGLOBAL \nEDITION\nFor these Global Editions, the editori

In [8]:
len(extracted_data)

1022

In [9]:
from typing import List
from langchain.schema import Document

def filter_to_minimal_docs(docs: List[Document])-> List[Document]:
    """
    Given a list of documents objects, return a list of document objects containing only 'source' in metadata and the original page_content.
    """
    minimal_docs: List[Document] = []
    for doc in docs:
        src = doc.metadata.get("source")
        minimal_docs.append(
            Document(
                page_content=doc.page_content,
                metadata={"source":src}
            )
        )
    return minimal_docs

In [10]:
minimal_docs = filter_to_minimal_docs(extracted_data)
minimal_docs

[Document(metadata={'source': 'data/1 Rafael C. Gonzales, Digital Image Processing.pdf'}, page_content='GLOBAL \nEDITION\nThis is a special edition of an established \ntitle widely used by colleges and universities \nthroughout the world. Pearson published this \nexclusive edition for the benefit of students \noutside the United States and Canada. If \nyou purchased this book within the United \nStates or Canada, you should be aware that \nit has been imported without the approval of \nthe Publisher or Author. The Global Edition \nis not supported in the United States and \nCanada.\nPearson Global Edition\nGLOBAL \nEDITION\nFor these Global Editions, the editorial team at Pearson has \ncollaborated with educators across the world to address a \nwide range of subjects and requirements, equipping students \nwith the best possible learning tools. This Global Edition \npreserves the cutting-edge approach and pedagogy of the \noriginal, but also features alterations, customization, and \nad

In [11]:
# chunking of document
def text_split(minimal_docs):
    text_splitter = RecursiveCharacterTextSplitter(
        chunk_size = 500,
        chunk_overlap=20
    )
    text_chunk = text_splitter.split_documents(minimal_docs)
    return text_chunk
    


In [12]:
text_chunk = text_split(minimal_docs)
print(f"Number of chunks: {len(text_chunk)}")

Number of chunks: 5728


In [15]:
import numpy
print(numpy.__version__)

1.26.4


In [16]:
from langchain.embeddings import HuggingFaceEmbeddings

def download_embeddings():
    model_name = "sentence-transformers/all-MiniLM-L6-v2"
    embeddings = HuggingFaceEmbeddings(
        model_name=model_name
    )
    return embeddings
embedding = download_embeddings()

/var/folders/j2/3h1p83z922767wcc7gn_sp4c0000gn/T/ipykernel_66788/922177244.py:5: LangChainDeprecationWarning: The class `HuggingFaceEmbeddings` was deprecated in LangChain 0.2.2 and will be removed in 1.0. An updated version of the class exists in the :class:`~langchain-huggingface package and should be used instead. To use it run `pip install -U :class:`~langchain-huggingface` and import as `from :class:`~langchain_huggingface import HuggingFaceEmbeddings``.
  embeddings = HuggingFaceEmbeddings(
/usr/local/Caskroom/miniconda/base/envs/minibot/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [17]:
embedding

HuggingFaceEmbeddings(client=SentenceTransformer(
  (0): Transformer({'max_seq_length': 256, 'do_lower_case': False}) with Transformer model: BertModel 
  (1): Pooling({'word_embedding_dimension': 384, 'pooling_mode_cls_token': False, 'pooling_mode_mean_tokens': True, 'pooling_mode_max_tokens': False, 'pooling_mode_mean_sqrt_len_tokens': False, 'pooling_mode_weightedmean_tokens': False, 'pooling_mode_lasttoken': False, 'include_prompt': True})
  (2): Normalize()
), model_name='sentence-transformers/all-MiniLM-L6-v2', cache_folder=None, model_kwargs={}, encode_kwargs={}, multi_process=False, show_progress=False)

In [38]:
from dotenv import load_dotenv
load_dotenv()

True

In [39]:
PINECONE_API_KEY=os.getenv("PINECONE_API_KEY")
OPENAI_API_KEY=os.getenv("OPENAI_API_KEY")

os.environ["PINECONE_API_KEY"] = PINECONE_API_KEY
os.environ["OPENAI_API_KEY"] = OPENAI_API_KEY

In [40]:
from pinecone import Pinecone
pinecone_api_key = PINECONE_API_KEY

pc = Pinecone(api_key=pinecone_api_key)
pc

In [45]:
from pinecone import ServerlessSpec
index_name = "studybot"

if not pc.has_index(index_name):
    pc.create_index(
        name=index_name,
        dimension=384,
        metric="cosine",
        spec=ServerlessSpec(cloud="aws",region="us-east-1")
    )
index = pc.Index(index_name)

In [46]:
# ***** DON'T USE twice for same document, o/w copies will be created! INSTEAD use next CODE TEMPLATE ****

# from langchain_pinecone import PineconeVectorStore

# docsearch = PineconeVectorStore.from_documents(
#     documents=text_chunk,
#     embedding=embedding,
#     index_name=index_name
# )


In [23]:
# load existing index

from langchain_pinecone import PineconeVectorStore

docsearch = PineconeVectorStore.from_existing_index(
    index_name=index_name,
    embedding=embedding
)

In [47]:
retriever = docsearch.as_retriever(search_type="similarity",search_kwargs={"k":3})

In [48]:
retrieved_docs = retriever.invoke("What is Line detection?")
retrieved_docs

[Document(id='61baadbf-52fc-4b0d-a225-18da6fe26d87', metadata={'source': 'data/1 Rafael C. Gonzales, Digital Image Processing.pdf'}, page_content='are surrounded by a homogeneous background in the area of the detector kernel. When this condition \nis not satisﬁed, other methods discussed in this chapter are more suitable for detecting intensity changes.\nLINE DETECTION\nThe next level of complexity is line detection. Based on the discussion earlier in this \nsection, we know that for line detection we can expect second derivatives to result \nin a stronger filter response, and to produce thinner lines than first derivatives. Thus,'),
 Document(id='3bfae356-9df2-4bc4-9ea5-fcd08e73c52e', metadata={'source': 'data/1 Rafael C. Gonzales, Digital Image Processing.pdf'}, page_content='702    Chapter 10  Image Segmentation\nwe are interested are isolated points, lines, and edges. Edge pixels are pixels at which \nthe intensity of an image changes abruptly, and edges (or edge segments) are sets

In [54]:
# from langchain_openai import ChatOpenAI

# chatModel = ChatOpenAI(model="gpt-4o")

from transformers import pipeline
from langchain_huggingface import HuggingFacePipeline

generator = pipeline(
    "text-generation",
    model="google/flan-t5-base",   # you can try flan-t5-large if you want better quality
    device=0                      
)
chatModel = HuggingFacePipeline(pipeline=generator)

Device set to use mps:0
The model 'T5ForConditionalGeneration' is not supported for text-generation. Supported models are ['PeftModelForCausalLM', 'ApertusForCausalLM', 'ArceeForCausalLM', 'AriaTextForCausalLM', 'BambaForCausalLM', 'BartForCausalLM', 'BertLMHeadModel', 'BertGenerationDecoder', 'BigBirdForCausalLM', 'BigBirdPegasusForCausalLM', 'BioGptForCausalLM', 'BitNetForCausalLM', 'BlenderbotForCausalLM', 'BlenderbotSmallForCausalLM', 'BloomForCausalLM', 'CamembertForCausalLM', 'LlamaForCausalLM', 'CodeGenForCausalLM', 'CohereForCausalLM', 'Cohere2ForCausalLM', 'CpmAntForCausalLM', 'CTRLLMHeadModel', 'Data2VecTextForCausalLM', 'DbrxForCausalLM', 'DeepseekV2ForCausalLM', 'DeepseekV3ForCausalLM', 'DiffLlamaForCausalLM', 'DogeForCausalLM', 'Dots1ForCausalLM', 'ElectraForCausalLM', 'Emu3ForCausalLM', 'ErnieForCausalLM', 'Ernie4_5ForCausalLM', 'Ernie4_5_MoeForCausalLM', 'Exaone4ForCausalLM', 'FalconForCausalLM', 'FalconH1ForCausalLM', 'FalconMambaForCausalLM', 'FuyuForCausalLM', 'GemmaF

In [55]:
from langchain.chains import create_retrieval_chain
from langchain.chains.combine_documents import create_stuff_documents_chain
from langchain_core.prompts import ChatPromptTemplate

In [57]:
system_prompt = (
    "You are a Teaching Assistant for question-answering tasks. based on book content "
    "Use the following pieces of retreived context to answer "
    "the question. If you don't know the answer, say that you "
    "don't know. Use ten sentences maximum and keep the answer concise and to the point, "
    "relating to the asked qustion "
    "\n\n"
    "{context}"
)

prompt = ChatPromptTemplate.from_messages(
    [
        ("system",system_prompt),
        ("human","{input}"),
    ]
)

In [58]:
question_answer_chain = create_stuff_documents_chain(chatModel, prompt)
rag_chain = create_retrieval_chain(retriever, question_answer_chain)

In [59]:
response = rag_chain.invoke({"input":"What is Line detection?"})
print(response["answer"])

/usr/local/Caskroom/miniconda/base/envs/minibot/lib/python3.10/site-packages/transformers/pytorch_utils.py:339: UserWarning: To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
  test_elements = torch.tensor(test_elements)


System: You are a Teaching Assistant for question-answering tasks. based on book content Use the following pieces of retreived context to answer the question. If you don't know the answer, say that you don't know. Use ten sentences maximum and keep the answer concise and to the point, relating to the asked qustion 

are surrounded by a homogeneous background in the area of the detector kernel. When this condition 
is not satisﬁed, other methods discussed in this chapter are more suitable for detecting intensity changes.
LINE DETECTION
The next level of complexity is line detection. Based on the discussion earlier in this 
section, we know that for line detection we can expect second derivatives to result 
in a stronger filter response, and to produce thinner lines than first derivatives. Thus,

702    Chapter 10  Image Segmentation
we are interested are isolated points, lines, and edges. Edge pixels are pixels at which 
the intensity of an image changes abruptly, and edges (or edge seg